### DistilBERT Model Exploration

In this section, we shift our focus to exploring the DistilBERT model, a lighter and faster version of the original BERT architecture. While DistilBERT aims to retain much of the knowledge and capabilities of BERT, it does so with fewer parameters and reduced computational requirements. This exploration is particularly relevant in scenarios where speed and efficiency are critical, such as real-time applications or resource-constrained environments.

**Model Implementation and Purpose**

Our implementation involves fine-tuning DistilBERT on the same dataset we used for the BERT model, aiming to evaluate its performance in the context of question answering. The goal is to see how well DistilBERT can understand and generate answers based on the provided context, even though it's widely recognized that it may not match BERT's performance in many cases.

**Key Features of the Code**

1. **Data Preparation**: Just like with BERT, we preprocess our data to ensure it's in the right format for DistilBERT. This includes tokenizing the questions and contexts, as well as padding them to ensure uniform input lengths.

2. **Model Training**: We set up the training loop, where DistilBERT is fine-tuned on our dataset. The training process involves adjusting the model's weights based on how well it predicts the answers, optimizing its understanding of the context.

3. **Evaluation & Testing**: Post-training, we evaluate the model using metrics such as ROUGE, BLEU, and F1 scores. These metrics provide insight into how accurately DistilBERT generates answers compared to the reference answers.

4. **Performance Analysis**: After evaluation, we will compare the performance of DistilBERT with that of the BERT model. This analysis will help us understand the trade-offs involved in using a distilled version of BERT, particularly in terms of response accuracy and computational efficiency.

**Conclusion and Future Directions**

It's important to note that we haven't invested extensive time in optimizing DistilBERT for our use case, given the general consensus that it often yields inferior performance compared to BERT. However, this exploration is valuable for understanding the potential benefits of using lighter models in appropriate contexts. Future work may involve further tuning and experimenting with different configurations to maximize DistilBERT's effectiveness, particularly in situations where computational resources are limited. By examining DistilBERT alongside BERT, we gain insights into the versatility and adaptability of transformer-based models for context-based question answering applications.


In [16]:
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
# Import Gaussian filter for smoothing
from scipy.ndimage import gaussian_filter1d
import json
import torch
from transformers import DistilBertTokenizerFast, DistilBertForQuestionAnswering, AdamW
from torch.utils.data import DataLoader, Dataset, random_split, default_collate
from torch.cuda.amp import autocast, GradScaler
import warnings
warnings.filterwarnings('ignore')

In [17]:
!pip install -q transformers

In [23]:
dataset_path = 'train-v1.1.json'

In [24]:
# Step 1: Initialize the tokenizer
tokenizer = DistilBertTokenizerFast.from_pretrained('distilbert-base-uncased')

# Custom dataset class for question-answering
class QADataset(Dataset):
    def __init__(self, examples):
        self.examples = examples
    
    def __len__(self):
        return len(self.examples)
    
    def __getitem__(self, idx):
        return self.examples[idx]

In [25]:
# Step 2: Preprocessing function for the dataset
def prepare_features(example):
    inputs = tokenizer(
        example['question'],
        example['context'],
        max_length=256,  # Reduced sequence length for faster processing
        truncation=True,
        padding="max_length",
        return_tensors="pt",
        return_offsets_mapping=True
    )

    if 'answers' not in example or len(example['answers']['answer_start']) == 0:
        return None

    start_char = example['answers']['answer_start'][0]
    end_char = start_char + len(example['answers']['text'][0])
    offset_mapping = inputs['offset_mapping'][0]

    try:
        start_pos = next(idx for idx, (start, end) in enumerate(offset_mapping) if start <= start_char < end)
        end_pos = next(idx for idx, (start, end) in enumerate(offset_mapping) if start < end_char <= end)
    except StopIteration:
        return None

    inputs['start_positions'] = torch.tensor([start_pos])
    inputs['end_positions'] = torch.tensor([end_pos])
    inputs.pop('offset_mapping')

    return {
        'input_ids': inputs['input_ids'].squeeze(),
        'attention_mask': inputs['attention_mask'].squeeze(),
        'start_positions': inputs['start_positions'].squeeze(),
        'end_positions': inputs['end_positions'].squeeze(),
    }

In [26]:
# Step 3: Load and preprocess the dataset
def load_dataset(dataset_path):
    with open(dataset_path, 'r') as f:
        dataset = json.load(f)
        examples = []
        for article in dataset['data']:
            for paragraph in article['paragraphs']:
                context = paragraph['context']
                for qa in paragraph['qas']:
                    question = qa['question']
                    answers = {
                        'answer_start': [ans['answer_start'] for ans in qa['answers']],
                        'text': [ans['text'] for ans in qa['answers']]
                    }
                    examples.append({
                        'context': context,
                        'question': question,
                        'answers': answers
                    })
        return examples


In [27]:
# Step 4: Preprocess the dataset examples for training
  
dataset_examples = load_dataset(dataset_path)
encoded_dataset = [prepare_features(example) for example in dataset_examples if prepare_features(example) is not None]


In [32]:
encoded_dataset[0]

{'input_ids': tensor([  101,  2000,  3183,  2106,  1996,  6261,  2984,  9382,  3711,  1999,
          8517,  1999, 10223, 26371,  2605,  1029,   102,  6549,  2135,  1010,
          1996,  2082,  2038,  1037,  3234,  2839,  1012, 10234,  1996,  2364,
          2311,  1005,  1055,  2751,  8514,  2003,  1037,  3585,  6231,  1997,
          1996,  6261,  2984,  1012,  3202,  1999,  2392,  1997,  1996,  2364,
          2311,  1998,  5307,  2009,  1010,  2003,  1037,  6967,  6231,  1997,
          4828,  2007,  2608,  2039, 14995,  6924,  2007,  1996,  5722,  1000,
          2310,  3490,  2618,  4748,  2033, 18168,  5267,  1000,  1012,  2279,
          2000,  1996,  2364,  2311,  2003,  1996, 13546,  1997,  1996,  6730,
          2540,  1012,  3202,  2369,  1996, 13546,  2003,  1996, 24665, 23052,
          1010,  1037, 14042,  2173,  1997,  7083,  1998,  9185,  1012,  2009,
          2003,  1037, 15059,  1997,  1996, 24665, 23052,  2012, 10223, 26371,
          1010,  2605,  2073,  1996,  6

In [28]:
# Step 5: Create PyTorch dataset
qa_dataset = QADataset(encoded_dataset)


In [29]:
# Step 6: Split into training and validation sets
train_size = int(0.9 * len(qa_dataset))
val_size = len(qa_dataset) - train_size
train_dataset, val_dataset = random_split(qa_dataset, [train_size, val_size])

def custom_collate_fn(batch):
    return default_collate([item for item in batch if item is not None])

train_dataloader = DataLoader(train_dataset, batch_size=16, shuffle=True, collate_fn=custom_collate_fn)
val_dataloader = DataLoader(val_dataset, batch_size=8, collate_fn=custom_collate_fn)


### Explanation of DistilBERT Question-Answering Pipeline

In this section, we outline the steps involved in preparing our dataset for fine-tuning the DistilBERT model on a question-answering task. This process is crucial for ensuring that the model receives the properly formatted input necessary for effective learning.

1. **Dataset Path Initialization**:
   We start by defining the path to the SQuAD1.1 dataset, which is a widely used dataset for training question-answering models. This JSON file contains questions, contexts, and corresponding answers that our model will learn from.

2. **Tokenizer Initialization**:
   We initialize the tokenizer for the DistilBERT model. This tokenizer converts text into a format that the model can understand, including input IDs and attention masks. By loading a pre-trained tokenizer, we ensure consistency with the DistilBERT vocabulary.

3. **Custom Dataset Class**:
   A custom dataset class is defined to handle our examples. This class allows us to easily manage the dataset, including determining its length and accessing individual examples based on their index.

4. **Preprocessing Function**:
   The preprocessing function is responsible for tokenizing each example (question and context) and generating the necessary input format for the model. It sets a maximum sequence length, handles padding and truncation, and calculates the start and end positions of answers within the context. This step is critical for training the model to locate answers in the text.

5. **Loading and Preprocessing the Dataset**:
   We load the dataset by reading the JSON file and extracting relevant data into a structured format. Each entry consists of a context, a question, and associated answers. This organization is essential for further processing.

6. **Encoding the Dataset Examples**:
   After loading the dataset examples, we encode each example using the preprocessing function, filtering out any that cannot be processed. This ensures that we retain only valid inputs for training.

7. **Creating the PyTorch Dataset**:
   We create an instance of our custom dataset class, passing in the encoded examples. This structure facilitates working with the dataset in PyTorch, allowing for straightforward data manipulation during training.

8. **Splitting the Dataset**:
   The dataset is split into training and validation sets, typically allocating 90% for training and 10% for validation. This division is crucial for evaluating the model's performance on unseen data during the training process.

9. **Custom Collate Function**:
   We define a custom collate function to handle batches of data, ensuring that only valid items are included in each batch. This prevents potential issues during the training phase.

10. **Creating DataLoaders**:
    Finally, we create `DataLoader` instances for both the training and validation datasets. These loaders facilitate batch processing, allowing us to efficiently feed data into the model in specified batch sizes.

### Summary

This code establishes a comprehensive pipeline for preparing data for fine-tuning the DistilBERT model on a question-answering task. By carefully preprocessing the dataset and structuring it for PyTorch, we set the stage for effective model training and evaluation. As we proceed with the training, we will be able to assess the performance of DistilBERT in understanding context and generating answers based on the provided questions and contexts.


### Model Training


In this section, we implement the training and evaluation process for a DistilBERT model tailored for question answering tasks.

1. **Model Initialization**: We load a pre-trained DistilBERT model, which provides a robust foundation for understanding language, and set up an optimizer to adjust the model's parameters during training.

2. **Device Setup**: We determine whether to use a GPU or CPU for training to maximize efficiency, enabling faster computations.

3. **Mixed Precision Training**: By employing mixed precision, we enhance training speed and reduce memory usage, allowing us to work with larger models or batch sizes.

4. **Training and Validation Functions**: We define functions for training and validating the model. The training function computes the loss and updates the model's weights, while the validation function evaluates model performance on a separate dataset to monitor its accuracy.

5. **Training Loop**: A loop executes the training and validation processes for a specified number of epochs, tracking and printing performance metrics to observe improvements over time.

6. **Model Saving**: After training, we save the trained model and tokenizer to a designated directory for future use.

This structured approach facilitates efficient training and evaluation of the DistilBERT model, ensuring it is well-prepared for real-world question-answering applications.


In [16]:
# Step 7: Initialize the model for Question Answering
model = DistilBertForQuestionAnswering.from_pretrained('distilbert-base-uncased')
optimizer = AdamW(model.parameters(), lr=3e-5)


model.safetensors:   0%|          | 0.00/268M [00:00<?, ?B/s]

Some weights of DistilBertForQuestionAnswering were not initialized from the model checkpoint at distilbert-base-uncased and are newly initialized: ['qa_outputs.bias', 'qa_outputs.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
/opt/conda/lib/python3.10/site-packages/transformers/optimization.py:591: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(


In [7]:
# Step 8: Set up the device for training
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
model.to(device)

DistilBertForQuestionAnswering(
  (distilbert): DistilBertModel(
    (embeddings): Embeddings(
      (word_embeddings): Embedding(30522, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (transformer): Transformer(
      (layer): ModuleList(
        (0-5): 6 x TransformerBlock(
          (attention): MultiHeadSelfAttention(
            (dropout): Dropout(p=0.1, inplace=False)
            (q_lin): Linear(in_features=768, out_features=768, bias=True)
            (k_lin): Linear(in_features=768, out_features=768, bias=True)
            (v_lin): Linear(in_features=768, out_features=768, bias=True)
            (out_lin): Linear(in_features=768, out_features=768, bias=True)
          )
          (sa_layer_norm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
          (ffn): FFN(
            (dropout): Dropout(p=0.1, inplace=False)
      

In [29]:


# Mixed precision scaler
scaler = GradScaler()


/tmp/ipykernel_30/590130087.py:6: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  scaler = GradScaler()


In [18]:
# Step 9: Define the training and validation functions with mixed precision
def train(model, dataloader, optimizer, device, scaler):
    model.train()
    total_loss = 0
    for batch in dataloader:
        input_ids = batch['input_ids'].to(device)
        attention_mask = batch['attention_mask'].to(device)
        start_positions = batch['start_positions'].to(device)
        end_positions = batch['end_positions'].to(device)

        optimizer.zero_grad()

        # Use autocast for mixed precision
        with autocast():
            outputs = model(input_ids, attention_mask=attention_mask, start_positions=start_positions, end_positions=end_positions)
            loss = outputs.loss
            total_loss += loss.item()

        # Scale the loss and backpropagate
        scaler.scale(loss).backward()
        scaler.step(optimizer)
        scaler.update()

    return total_loss / len(dataloader)

def validate(model, dataloader, device):
    model.eval()
    total_loss = 0
    correct = 0
    total = 0
    with torch.no_grad():
        for batch in dataloader:
            input_ids = batch['input_ids'].to(device)
            attention_mask = batch['attention_mask'].to(device)
            start_positions = batch['start_positions'].to(device)
            end_positions = batch['end_positions'].to(device)

            outputs = model(input_ids, attention_mask=attention_mask, start_positions=start_positions, end_positions=end_positions)
            loss = outputs.loss
            total_loss += loss.item()

            # Get the predicted start and end positions
            start_preds = torch.argmax(outputs.start_logits, dim=1)
            end_preds = torch.argmax(outputs.end_logits, dim=1)

            # Calculate accuracy: Check if both start and end positions are correct
            correct += ((start_preds == start_positions) & (end_preds == end_positions)).sum().item()
            total += input_ids.size(0)

    avg_loss = total_loss / len(dataloader)
    accuracy = correct / total if total > 0 else 0
    return avg_loss, accuracy


In [12]:
# Step 10: Training Loop with accuracy printing
num_epochs = 3  # Reduced number of epochs for faster results
total_accuracy = 0  # To track cumulative accuracy across epochs

for epoch in range(num_epochs):
    avg_train_loss = train(model, train_dataloader, optimizer, device, scaler)
    avg_val_loss, val_accuracy = validate(model, val_dataloader, device)
    
    # Accumulate total accuracy over all epochs
    total_accuracy += val_accuracy
    
    print(f"Epoch {epoch+1}/{num_epochs}, Training Loss: {avg_train_loss:.4f}, Validation Loss: {avg_val_loss:.4f}, Validation Accuracy: {val_accuracy:.4f}")

# Print the cumulative accuracy over all epochs
avg_total_accuracy = total_accuracy / num_epochs
print(f"\nTotal Average Validation Accuracy over {num_epochs} epochs: {avg_total_accuracy:.4f}")


/tmp/ipykernel_30/3732227169.py:14: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with autocast():


Epoch 1/3, Training Loss: 1.7261, Validation Loss: 1.3148, Validation Accuracy: 0.4825
Epoch 2/3, Training Loss: 1.1330, Validation Loss: 1.3120, Validation Accuracy: 0.4916
Epoch 3/3, Training Loss: 0.8496, Validation Loss: 1.3419, Validation Accuracy: 0.4988

Total Average Validation Accuracy over 3 epochs: 0.4910


In [24]:
# Define the directory where you want to save the model
model_save_path = 'DISTILBERT_model'

# Create the directory if it doesn't exist
if not os.path.exists(model_save_path):
    os.makedirs(model_save_path)


# Save the trained model and tokenizer
model.save_pretrained(model_save_path)
tokenizer.save_pretrained(model_save_path)

('squad-distilbert-trained/DISTILBERT_model/tokenizer_config.json',
 'squad-distilbert-trained/DISTILBERT_model/special_tokens_map.json',
 'squad-distilbert-trained/DISTILBERT_model/vocab.txt',
 'squad-distilbert-trained/DISTILBERT_model/added_tokens.json',
 'squad-distilbert-trained/DISTILBERT_model/tokenizer.json')

In [2]:

# # Compress the model directory into a zip file
# !zip -r distilbertmodel.zip squad-distilbert-trained/DISTILBERT_model

# # Download the zip file to your local system
# from IPython.display import FileLink

# # Display a link to download the file
# FileLink(r'distilbertmodel.zip')


### Post Code Summary

In this section, we perform the initialization, training, and validation of the DistilBERT model specifically designed for question answering tasks using the `DistilBertForQuestionAnswering` class from the Hugging Face Transformers library.

1. **Model Initialization**: 
   - We load the pre-trained DistilBERT model, which has been fine-tuned on the SQuAD dataset, making it well-suited for extracting answers from a given context based on a specific question. The model is initialized with a learning rate of `3e-5` to ensure stable convergence during training.

2. **Optimizer Setup**: 
   - The AdamW optimizer is employed to improve weight updates during training, accounting for weight decay, which helps prevent overfitting.

3. **Device Configuration**: 
   - We check for GPU availability and move the model to the appropriate device (GPU or CPU) for faster training. This is critical for handling larger datasets efficiently.

4. **Mixed Precision Training**: 
   - To optimize performance and reduce memory usage, we implement mixed precision training using PyTorch's GradScaler and autocast functions. This technique allows the model to use half-precision floating-point numbers where applicable, significantly speeding up training without sacrificing much in terms of model accuracy.

5. **Training Function**: 
   - The training function iterates through the training data, calculating the loss for each batch. We use the model’s outputs to compute the loss based on the start and end positions of the answers. The loss is scaled and backpropagated, and the optimizer updates the model weights.

6. **Validation Function**: 
   - The validation function assesses the model's performance on a separate validation dataset. It calculates the loss and accuracy by comparing the predicted start and end positions with the true labels. This step helps gauge the model's ability to generalize beyond the training data.

7. **Training Loop**: 
   - Over three epochs, we track the average training loss, validation loss, and validation accuracy. The training loss decreases over epochs, indicating that the model is learning; however, validation loss fluctuates slightly, suggesting that the model might not be fully converging and could benefit from additional training or tuning.

8. **Model Saving**: 
   - After completing the training process, we save the fine-tuned model and tokenizer to a specified directory (`DISTILBERT_model`). This step ensures that the trained model can be easily loaded for inference or further training without the need to retrain from scratch.

Overall, this implementation showcases a structured approach to fine-tuning a DistilBERT model for question answering tasks, leveraging modern techniques like mixed precision training to enhance performance and efficiency.


### Evaluation & Testing



In [4]:
tokenizer=DistilBertTokenizerFast.from_pretrained('DISTILBERT_model')
model = DistilBertForQuestionAnswering.from_pretrained('DISTILBERT_model')

In [5]:
# Step 12: Prediction function
def predict(context, question):
    inputs = tokenizer(question, context, max_length=256, truncation=True, padding="max_length", return_tensors="pt").to(device)
    model.eval()
    with torch.no_grad():
        outputs = model(**inputs)
        start_scores = outputs.start_logits
        end_scores = outputs.end_logits

        start_idx = torch.argmax(start_scores)
        end_idx = torch.argmax(end_scores)

        input_ids = inputs['input_ids'].squeeze().tolist()
        answer_tokens = input_ids[start_idx:end_idx + 1]
        answer = tokenizer.decode(answer_tokens)

    return answer


In [8]:
context = "India is a country located in South Asia. Its captial is New Delhi."
question = "What is the capital of India?"

predicted_answer = predict(context, question)
print("Predicted Answer:", predicted_answer)

Predicted Answer: new delhi


In [9]:
context = "Architecturally, the school has a Catholic character. Atop the Main Building's gold dome is a golden statue of the Virgin Mary. Immediately in front of the Main Building and facing it, is a copper statue of Christ with arms upraised with the legend \"Venite Ad Me Omnes\". Next to the Main Building is the Basilica of the Sacred Heart. Immediately behind the basilica is the Grotto, a Marian place of prayer and reflection. It is a replica of the grotto at Lourdes, France where the Virgin Mary reputedly appeared to Saint Bernadette Soubirous in 1858. At the end of the main drive (and in a direct line that connects through 3 statues and the Gold Dome), is a simple, modern stone statue of Mary."
question = "To whom did the Virgin Mary allegedly appear in 1858 in Lourdes France?"

predicted_answer = predict(context, question)
print("Predicted Answer:", predicted_answer)

Predicted Answer: saint bernadette soubirous


In [10]:

context = '''Music is an art form whose medium is sound and silence. It is a universal language that 
can evoke emotions, convey messages, and bring people together. Music has been an 
integral part of human culture for centuries, with various genres and styles emerging 
across the world. From classical to contemporary, music has the power to inspire, heal, 
and entertain.'''

question = "What is the difference between Music and Harmony?"

predicted_answer = predict(context, question)
print("Predicted Answer:", predicted_answer)

Predicted Answer: music has the power to inspire, heal, and entertain


In [11]:
context = "Pappu is from america. He is from california"
question = "which country is pappu from?"

predicted_answer = predict(context, question)
print("Predicted Answer:", predicted_answer)

Predicted Answer: california


In [48]:
from nltk.translate.bleu_score import sentence_bleu
from rouge_score import rouge_scorer

# Example inputs
context = """Music is an art form whose medium is sound and silence. It is a universal language that 
can evoke emotions, convey messages, and bring people together. Music has been an 
integral part of human culture for centuries, with various genres and styles emerging 
across the world. From classical to contemporary, music has the power to inspire, heal, 
and entertain."""

question = "What is the difference between Music and Harmony?"

# Define actual and predicted answers
actual_answer = "Music is an art form and harmony refers to the combination of sounds."
predicted_answer = "music has the power to inspire, heal, and entertain"

# Normalize answers (lowercase)
actual_answer = actual_answer.lower().strip()
predicted_answer = predicted_answer.lower().strip()

# Calculate BLEU score
bleu_score = sentence_bleu([actual_answer.split()], predicted_answer.split(), weights=(1.0, 0.0, 0.0, 0.0))

# Calculate ROUGE scores
scorer = rouge_scorer.RougeScorer(['rouge1', 'rouge2', 'rougeL'], use_stemmer=True)
rouge_scores = scorer.score(actual_answer, predicted_answer)

# Calculate F1 score based on ROUGE-1 precision and recall
precision = rouge_scores['rouge1'].precision
recall = rouge_scores['rouge1'].recall
if precision + recall > 0:  # Avoid division by zero
    f1_score = 2 * (precision * recall) / (precision + recall)
else:
    f1_score = 0.0

# Print the results
print(f"Predicted Answer: {predicted_answer}")
print(f"Actual Answer: {actual_answer}")
print(f"BLEU Score: {bleu_score:.4f}")
print(f"ROUGE-1 F1 Score: {rouge_scores['rouge1'].fmeasure:.4f}")
print(f"ROUGE-2 F1 Score: {rouge_scores['rouge2'].fmeasure:.4f}")
print(f"ROUGE-L F1 Score: {rouge_scores['rougeL'].fmeasure:.4f}")
print(f"F1 Score: {f1_score:.4f}")


Predicted Answer: music has the power to inspire, heal, and entertain
Actual Answer: music is an art form and harmony refers to the combination of sounds.
BLEU Score: 0.2850
ROUGE-1 F1 Score: 0.3636
ROUGE-2 F1 Score: 0.0000
ROUGE-L F1 Score: 0.1818
F1 Score: 0.3636


### Results Summary

**Predicted Answer**: music has the power to inspire, heal, and entertain  
**Actual Answer**: music is an art form and harmony refers to the combination of sounds.  
**BLEU Score**: 0.2850  
**ROUGE-1 F1 Score**: 0.3636  
**ROUGE-2 F1 Score**: 0.0000  
**ROUGE-L F1 Score**: 0.1818  
**F1 Score**: 0.3636  

These results indicate that DistilBERT is not performing well at the current level of fine-tuning. The low scores suggest it may require more extensive training to improve its ability to generate accurate and relevant answers.
